In [196]:
import math
import random
import copy
import matplotlib.pyplot as plt
import matplotlib.patches as patches
from matplotlib import animation, rc, gridspec
from IPython.display import HTML

N = 7  # エージェントの種類ごとの個数
SIZE = N   # 仮想空間のサイズ
OBJSIZE = [SIZE * 4.5 / 10, SIZE * 4 / 10 , SIZE * 3 / 10, SIZE * 2 / 10] # xの座標,yの座標,幅,高さ　
TIMELIMIT = 200  # シミュレーションの打ち切り時刻
SEED = 65535  # 乱数の初期化
SPEED = N/50  # エージェントの標準歩幅
AGENT_TYPES_AND_SPEED = {"Agent1" : 1,"Agent2" : 1.3,"Agent3" : 0.7,"Agent4" : 1,"Agent5" : 1.3,"Agent6" : 0.7} # エージェントの種類ごとのスピード変化
CH_DIR_DGR = 30 # 次の移動方向を決める際に変化する角度の最大値　ex) 30 => 最大で30度しか曲がらない
R = 0 # 衝突範囲
IS_STACK = False #　詰まった時の停止処理を入れるかどうか
IS_AGENT_COLLISION = False # エージェント同士の衝突処理を入れるかどうか
IS_ONETIME_OBJ_COLLISION = True # 障害物にぶつかった際の方向判定処理を1回のみにするかどうか

#Agent class
class Agent:

    def __init__(self, state, agent_type, speedvariable):
        self.state = state  # 状態の設定（Start or Left or Right）
        self.x = SIZE / 2  # x座標の中央
        self.y = SIZE / 20  # y座標の初期値は0
        self.my_radian = math.radians(random.randint(1,180)) # 1~180度の間でランダム
        self.x_v = math.cos(self.my_radian)*SPEED  # x方向の速さ
        self.y_v = math.sin(self.my_radian)*SPEED  # y方向の速さ
        self.term = 0  # スタートからの時間経過
        self.goaled = False
        self.collide = False
        self.collide_count = 0
        self.obj_collide = False # 障害物に当たっている
        self.x_v_obj_collide = 0 # 障害物に下から接している場合のx速度
        self.agent_type = agent_type# エージェントの種類
        self.speedvariable = speedvariable #エージェントの種類ごとのスピード変化値

    def _calcnext(self, agents):  # 次時刻の計算
        self._state_S(agents)  # 状態S用の計算


    def side_collision(self): #左右での衝突時の処理
        #現在の横方向移動の反転
        self.x_v = -1 * self.x_v
        #移動方向の反転
        self.my_radian = math.radians(180) - self.my_radian
        self.collide_count += 1 

    def around_object(self):
        
        #次の移動先が障害物内の時
        if OBJSIZE[0] < self.x + self.x_v < OBJSIZE[0] + OBJSIZE[2] and \
           OBJSIZE[1] < self.y + self.y_v < OBJSIZE[1] + OBJSIZE[3]:
           #横から衝突の場合　反発する
            if OBJSIZE[1] < self.y < OBJSIZE[1] + OBJSIZE[3]:
                self.side_collision()
            else:
                if IS_ONETIME_OBJ_COLLISION:
                    if not self.obj_collide: # 最初の1回のみ判定する
                        #下から衝突の場合 左右に避ける
                        self.obj_collide = True

                            # 確率で左に移動
                        if random.randint(1,100) < 67:
                            self.x_v_obj_collide = -1 * SPEED
                        else:
                            self.x_v_obj_collide = SPEED

                    # 障害物に下から接触した場合、初めて接触した時の方向を踏襲する
                    if self.obj_collide:
                        self.y_v = 0
                        self.x_v = self.x_v_obj_collide
                else:
                    self.obj_collide = True
                    # 障害物にぶつかるたびに確率で左に移動
                    if random.randint(1,100) < 67:
                        self.x_v_obj_collide = -1 * SPEED
                    else:
                        self.x_v_obj_collide = SPEED

                    if self.obj_collide:
                        self.y_v = 0
                        self.x_v = self.x_v_obj_collide
                    self.obj_collide = False

            self.collide_count += 1

        #状態がStartで、障害物の横にいる場合に、状態を変更する
        if self.state == "Start":
            if  OBJSIZE[1] < self.y + self.y_v < OBJSIZE[1] + OBJSIZE[3]: # yが障害物のｙ範囲内に入っているとき

                if self.x <= OBJSIZE[0] : # 左の時
                    self.state = "Left"
                elif self.x > OBJSIZE[0] + OBJSIZE[2] : # 右の時 
                    self.state = "Right"

    def _update_xy(self):
        """
        衝突判定　=>　左右壁判定　=>　ゴール判定
        エージェントの移動方向をランダムで変更する
        エージェントのxy座標を更新する
        """


        self.my_radian = math.radians(random.randint(int(max([0, (math.degrees(self.my_radian) - CH_DIR_DGR)])), int(min([180, (math.degrees(self.my_radian) + CH_DIR_DGR)])))) # 1~180度の間で前回値からch_dir_dgr分変化する
        self.x_v = math.cos(self.my_radian)*SPEED * self.speedvariable  # x方向の速さ
        self.y_v = math.sin(self.my_radian)*SPEED * self.speedvariable # y方向の速さ
        
        self.around_object()


        # 衝突判定　衝突していたら、確率で左に移動
        if self.collide:
          self.y_v = 0
          if random.randint(1,100) < 67:
            self.x_v = -1 * SPEED * self.speedvariable
          else:
            self.x_v = SPEED * self.speedvariable

          #衝突処理をしたのでリセット
          self.collide = False
          self.collide_count += 1
        # 左右壁判定　右にぶつかったら左に、左にぶつかったら右に、というようにする
        if self.x + self.x_v < 0 or SIZE < self.x + self.x_v:
            self.side_collision()

        # ゴール判定　Y軸で外に出たら消滅させる
        if self.y + self.y_v < 0 or SIZE < self.y + self.y_v:
            # self.y_v *= -1
            self.goaled = True
        #
        #  STACK処理
        #2回以上接触=>方向転換をしている場合、スタックしていると見て、1フレーム休み
        if self.collide_count > 1 and IS_STACK:
            pass
        else:
            self.x = self.x + self.x_v
            self.y = self.y + self.y_v

        self.collide_count = 0

    def _state_S(self, agents):  # 状態Sの計算メソッド


        # カテゴリ1のすべてのエージェントとの距離を調べる
        sx = self.x  # 状態Sのx座標
        sy = self.y  # 状態Sのy座標
        #障害物範囲内にいるか判定

        for i in range(len(agents)):
            ax = agents[i].x  # 抽出したstate1のx座標
            ay = agents[i].y  # 抽出したstate1のx座標
            aR = R # 衝突範囲の設定
   


            if (sx-ax)*(sx-ax) + (sy-ay)*(sy-ay) < aR:  # 指定した範囲内に状態Sがいる場合
                #接触フラグ
                if IS_AGENT_COLLISION:
                    self.collide = True

                break

        # xy座標を更新
        self._update_xy()



  # agentクラスの定義終わり


def calcn(agents):
    """次時刻の状態を計算"""
    # 状態Sのデータ
    xlistS, ylistS = [], []
    # 状態Iのデータ
    xlistL, ylistL = [], []
    # 状態Rのデータ
    xlistR, ylistR = [], []

    for i in range(len(agents)):
        agents[i]._calcnext(agents)

        # ゴールしたエージェントを除外
        if agents[i].goaled:
          continue

        # グラフデータに現在位置を追加
        if agents[i].state == "Start":
            xlistS.append(agents[i].x)
            ylistS.append(agents[i].y)
        elif agents[i].state == "Left":
            xlistL.append(agents[i].x)
            ylistL.append(agents[i].y)
        elif agents[i].state == "Right":
            xlistR.append(agents[i].x)
            ylistR.append(agents[i].y)
        else:
            raise ValueError(f"agentのstateが想定外の値になっています: {agents[i].state}")

    return xlistS, ylistS, xlistL, ylistL, xlistR, ylistR
    # calcn()関数の終わり



def scatter_plot(image, n, xlistS, ylistS, xlistL, ylistL, xlistR, ylistR):
    """散布図描画用関数"""
    """ラベル分類する"""
    image += ax[n].plot(xlistS, ylistS, ".", markersize=12, label="Start", color="k", alpha=0.5) #状態Sのプロット
    image += ax[n].plot(xlistL, ylistL, ".", markersize=12, label="Left", color="b") #状態Iのプロット
    image += ax[n].plot(xlistR, ylistR, ".", markersize=12, label="Right", color="g", alpha=0.5) #状態Rのプロット
    return image

# 初期化
random.seed(SEED) # 乱数の初期化
# 状態StartのエージェントをN個生成
agentsA = []
for key, item in AGENT_TYPES_AND_SPEED.items():
    agentsA += [Agent("Start", key, item) for i in range(N)]




# グラフデータの初期化
T = []
# Statas数推移
statasS_sum_left= []
statasL_sum_left= []
statasR_sum_left= []
statasD_sum_left= []
statasS_sum_right= []
statasL_sum_right= []
statasR_sum_right= []
statasD_sum_right= []

#描画するグラフの設定
fig = plt.figure(figsize=(5,5))
gs = gridspec.GridSpec(3, 1, height_ratios=(4, 1,1))
# ax = [plt.subplot(gs[0, 0]),plt.subplot(gs[1, 0])]
ax = [plt.subplot(gs[0, 0]),plt.subplot(gs[1, 0]),plt.subplot(gs[2, 0])]




#空のグラフが出てしまうのを回避
plt.close()

#アニメーション用のグラフ保管場所
ims = []

legend_flag = True  # 凡例描画のフラグ

#障害物の描画
r = patches.Rectangle(xy=(OBJSIZE[0], OBJSIZE[1]), width=OBJSIZE[2], height=OBJSIZE[3], ec='#000000', fill=False)



# エージェントシミュレーション
for t in range(TIMELIMIT):
    T.append(t)
    xlistS, ylistS, xlistL, ylistL, xlistR, ylistR = calcn(agentsA)  # 次時刻の状態を計算
    im = []


    # subplot0：散布図
    im += scatter_plot(im, 0, xlistS, ylistS, xlistL, ylistL, xlistR, ylistR)

    # subplot2：推移図
    statasS_sum_left.append(len(xlistS))
    statasL_sum_left.append(len(xlistL))
    statasR_sum_left.append(len(xlistR))
    im += ax[1].stackplot(T, statasL_sum_left, statasR_sum_left, statasS_sum_left, colors=["b", "g", "k"], alpha=0.7) # {'b', 'g', 'r', 'c', 'm', 'y', 'k', 'w'} 



    #描画設定
    if legend_flag:  # 一回のみ凡例を描画\
        ax[0].legend(loc='upper center', bbox_to_anchor=(0.5,1.2),  ncol=4, fontsize=8) #凡例の大きさ
        ax[0].set_xlim(0, SIZE)
        ax[0].set_ylim(0, SIZE)
        ax[0].tick_params(labelbottom=False,labelleft=False,labelright=False,labeltop=False, length=0)
        ax[0].tick_params(length=0)
        ax[0].set_title("")
        ax[0].add_patch(r)
        legend_flag = False

    ims.append(im)

# subplot3 : データテーブル

row_labels = list(AGENT_TYPES_AND_SPEED.keys())
column_labels=["Left", "Right"]
data = []



for label in row_labels:
    ls = [x for x in agentsA if x.agent_type == label]
    cnt0 = len( [ x for x in ls if x.state == column_labels[0] ])
    cnt1 = len( [ x for x in ls if x.state == column_labels[1] ])
    data.append([cnt0, cnt1])

ax[2].axis('tight')
ax[2].axis('off')

ax[2].table(cellText=data, rowLabels = row_labels, colLabels=column_labels,loc="center")

fig.subplots_adjust(hspace=0.3)
ani = animation.ArtistAnimation(fig, ims, interval=70)

rc('animation', html='jshtml')

ani

6カテゴリ 7体ずつ投入
左に言ったら青、右に言ったら緑
各カテゴリのエージェント、右と左に言った数を表示